In [ ]:
import pandas as pd
import numpy as np
from sklearn.decomposition import PCA
from matplotlib import pyplot as plt
from matplotlib.gridspec import GridSpec
from scipy import stats
from scipy.cluster.hierarchy import dendrogram, linkage

COLORS = {'MIOL': '#6e750e',
          'XEAT': '#06c2ac',
          'LECO': '#0485d1',
          'MAVI': '#dbb40c',
          'PSPI': '#000000',
          'CEME': '#ff796c',
          'CECO': '#be0119'
          }

SAMPLES = [
    'LECO1S',
    'LECO2S',
    'LECO3S',
    'LECO1P',
    'LECO2P',
    'LECO3P',
    'MAVI1S',
    'MAVI2S',
    'MAVI3S',
    'MAVI1P',
    'MAVI2P',
    'MAVI3P',
    'CECO1S',
    'CECO2S',
    'CECO3S',
    'CECO1P',
    'CECO2P',
    'CECO3P',
    'XEAT1S',
    'XEAT2S',
    'XEAT3S',
    'XEAT1P',
    'XEAT2P',
    'XEAT3P',
    'PSPI1S',
    'PSPI2S',
    'PSPI3S',
    'PSPI1P',
    'PSPI2P',
    'PSPI3P',
    'CEME1S',
    'CEME2S',
    'CEME3S',
    'CEME1P',
    'CEME2P',
    'CEME3P',
    'MIOL1S',
    'MIOL2S',
    'MIOL3S',
    'MIOL1P',
    'MIOL2P',
    'MIOL3P'
    ]

FASTWING = ['MAVI', 'CEME', 'CECO']
SAMPLECOLORS = [COLORS[x[:4]] for x in SAMPLES]
SAMPLESHAPES = ['o' if x[-1] == 'S' else 'v' for x in SAMPLES]
SPECIES = ['MAVI', 'CEME', 'CECO', 'LECO', 'XEAT', 'PSPI', 'MIOL']

dfx = pd.read_csv("Pease2022.counttable.csv", index_col=0)
dfx = dfx.filter(regex="[123][SP]", axis=1)
#CPM TRANSFORM
dfx = (dfx / dfx.sum()) * 1e6 
fig = plt.figure(figsize=(3.5, 2))
for i, abbrev in ((1, 'SH'), (2, 'PEC')):
    df = dfx.filter(regex="[123][{}]".format(abbrev[0]), axis=1)
    pca = PCA(n_components=2)
    pcom = pca.fit(df)
    XSAMPLES = [x for x in SAMPLES if x[-1] == abbrev[0]]
    XSAMPLESHAPES = ['*' if x[:4] in FASTWING else 'o' for x in XSAMPLES]
    if abbrev == 'PEC':
        XSAMPLESHAPES = ['*' if x[:4] in FASTWING else 'v' for x in XSAMPLES]
    XSAMPLECOLORS = [COLORS[x[:4]] for x in XSAMPLES]
    ax = fig.add_subplot(1, 2, i)
    ax.set_xlabel('PC1 ({:.1f}%)'.format(pcom.explained_variance_ratio_[0] * 100),
                  fontsize=6)
    ax.set_ylabel('PC2 ({:.1f}%)'.format(pcom.explained_variance_ratio_[1] * 100),
                  fontsize=6)
    ax.set_title(abbrev, fontsize=8)
    ax.tick_params(axis='both', labelsize=6) 
    for xcoord, ycoord, label, color, shape in zip(
        pca.components_[0], pca.components_[1],
            XSAMPLES, XSAMPLECOLORS, XSAMPLESHAPES):
        ax.scatter(xcoord, ycoord,
                   marker=shape,
                   c=color, s=10,
                   label=label if label[4] == '1' else '')
    ax.grid()
plt.tight_layout()
#plt.savefig("pecsh_pca2panel.pdf")

plt.show()

In [ ]:
from matplotlib import pyplot as plt
import pandas as pd
import numpy as np
from matplotlib import cm
from matplotlib.colors import ListedColormap, LinearSegmentedColormap
from matplotlib import colors

lmpcc_dfpaml = pd.read_csv('Pease2022.PAML.M5.csv',
                     delimiter=',', header=0, index_col=1, quotechar='"')
mpcc_dfpaml = pd.read_csv('Pease2022.PAML.M4.csv',
                     delimiter=',', header=0, index_col=1, quotechar='"')
mavi_dfpaml = pd.read_csv('Pease2022.PAML.MV.csv',
                     delimiter=',', header=0, index_col=1, quotechar='"')
cera_dfpaml = pd.read_csv('Pease2022.PAML.CE.csv',
                     delimiter=',', header=0, index_col=1, quotechar='"')

dfphy = pd.read_csv('Pease2022.PhyDGET_results.csv',
                    delimiter=',', header=0, index_col=0, quotechar='"')

genes_to_filter = [line.rstrip() for line in open('Pease2022.PAML_excluded_genes.txt').readlines()]

df_lmpcc = pd.merge(lmpcc_dfpaml, dfphy.filter(('deltaL.M5.SH', 'deltaL.M5.PC')), left_index=True, right_index=True)
df_mpcc = pd.merge(mpcc_dfpaml, dfphy.filter(('deltaL.M4.SH', 'deltaL.M4.PC')), left_index=True, right_index=True)
df_mavi = pd.merge(mavi_dfpaml, dfphy.filter(('deltaL.MV.SH', 'deltaL.MV.PC')), left_index=True, right_index=True)
df_cera = pd.merge(cera_dfpaml, dfphy.filter(('deltaL.CE.SH', 'deltaL.CE.PC')), left_index=True, right_index=True)

df_lmpcc = df_lmpcc.loc[~df_lmpcc.index.isin(genes_to_filter)]
df_mpcc = df_mpcc.loc[~df_mpcc.index.isin(genes_to_filter)]
df_mavi = df_mavi.loc[~df_mavi.index.isin(genes_to_filter)]
df_cera = df_cera.loc[~df_cera.index.isin(genes_to_filter)]


dfphy2 = dfphy.copy()
for row in dfphy2.iterrows():
    dfphy2.loc[row[0], 'maxcpm'] = (
        round(2 ** row[1].filter(regex=".*\.nrm").max(), 1))
#fillna(-2)

#dfphy2 = dfphy2.filter()


fig, ax = plt.subplots(2, 2, figsize=(6,6), sharey=False, sharex=False)



#### M5 GENE DIFFS
dxm5 = pd.read_csv(
    'Pease2022.NSpatterns.M5.csv',
     delimiter='\t', header=0, index_col=0, quotechar='"')

dxm5 = dxm5.join(dfphy2, how='right')
dxm5 = dxm5.fillna(0)
dxm5 = dxm5[dxm5['maxcpm'] > 2]
dxm5['nonsynonymous_changes'] = dxm5['nonsynonymous_changes'].clip(upper=7)
    
#### M4 GENE DIFFS
dxm4 = pd.read_csv(
    'Pease2022.NSpatterns.M4.csv',
     delimiter='\t', header=0, index_col=0, quotechar='"')

dxm4 = dxm4.join(dfphy2, how='right')
dxm4 = dxm4.fillna(0)
dxm4 = dxm4[dxm4['maxcpm'] > 2]

#### MV GENE DIFFS
dxmv = pd.read_csv(
    'Pease2022.NSpatterns.MV.csv',
     delimiter='\t', header=0, index_col=0, quotechar='"')

dxmv = dxmv.join(dfphy2, how='right')
dxmv = dxmv.fillna(0)
dxcmv = dxmv[dxmv['maxcpm'] > 2]
dxmv['nonsynonymous_changes'] = dxmv['nonsynonymous_changes'].clip(upper=7)

#### CE GENE DIFFS
dxce = pd.read_csv(
    'Pease2022.NSpatterns.CE.csv',
     delimiter='\t', header=0, index_col=0, quotechar='"')

dxce = dxce.join(dfphy2, how='right')
dxce = dxce.fillna(0)
dxce = dxce[dxce['maxcpm'] > 2]
dxce['nonsynonymous_changes'] = dxce['nonsynonymous_changes'].clip(upper=7)

kdata = "dN"
norm=colors.Normalize(vmin=0,vmax=10)
newcolors = [(0,0,0,0.3)] * 19 + ['dodgerblue'] * 11 + ['orange'] * 90 + ['magenta'] * 80
cmap=ListedColormap(newcolors)
nbin = 50
for i, model in enumerate(("M5", "M4", "MV", "CE")):
    #for k, tissue in enumerate(("SH",)):
    tissue = 'SH'
    treatment = "deltaL.{}.{}".format(model, tissue)
    j = [0,1,0,1][i]
    k = [0,0,1,1][i]
    zdf = [df_lmpcc, df_mpcc, df_mavi, df_cera][i]

    zdf.loc[zdf['N*dN'] < 2, 'dN/dS'] = 0
    ydf = zdf[zdf['dN/dS'] <= 1]
    zdf = zdf[zdf['dN/dS'] > 1]
    ax[j,k].scatter(ydf[kdata], ydf[treatment],
                    c=ydf['dN/dS'], 
                    norm=norm, cmap=cmap, s=ydf['dN']*(
                        1000 if j in (0,2) else 3000) + ydf[treatment],
                    edgecolors=([]))
    ax[j,k].scatter(zdf[kdata], zdf[treatment],
            c=zdf['dN/dS'], 
            norm=norm, cmap=cmap, s=zdf['dN']*(
                1000 if j in (0,2) else 3000) + zdf[treatment],
            zorder=10,
            edgecolors=([]))
    if j in (0, ):
        ax[j,k].set_xlim(-0.003,0.07)
        ax[j, k].plot((-0.003,0.07), (1.5, 1.5), 'k:',  linewidth=0.5)
        ax[j, k].plot((-0.003,0.07), (0, 0), 'k-',  linewidth=0.5)
    elif j in (1, ):
        ax[j,k].set_xlim(-0.001,0.025)
        ax[j,k].set_xticks([0.000, 0.005, 0.010, 0.015, 0.02])
        ax[j, k].plot((-0.001,0.25), (1.5, 1.5), 'k:',  linewidth=0.5)
        ax[j, k].plot((-0.001,0.25), (0, 0), 'k-', linewidth=0.5)
    ax[j, k].set_ylim(-1.5,4)


fig.tight_layout()
#plt.savefig("dndsplo2.png", dpi=300)
plt.show()



In [ ]:
import csv
from matplotlib import pyplot as plt
from matplotlib import cm
import matplotlib.colors as mcolors
import numpy as np
import pandas as pd
from IPython.display import display, Markdown, Latex
from matplotlib.markers import MarkerStyle
from itertools import chain

DATAORDER = ["deltaL.M6",
             "deltaL.M5",
             "deltaL.M4",
             "deltaL.MCC1",
             "deltaL.MCC2",
             "deltaL.R41",
             "deltaL.R42",
             "deltaL.R51",
             "deltaL.R52",
             "deltaL.XA",
             "deltaL.LC",
             "deltaL.MV",
             "deltaL.PP",
             "deltaL.CE"]

DATAORDER = [x + ".SH" for x in DATAORDER] + [x + ".PC" for x in DATAORDER]
MODELCOLOR = ['orange' if x.endswith('.SH') else 'blue' for x in DATAORDER]

m = MarkerStyle("d")
m._transform.rotate_deg(90)

PC_SAMPLES = {
   "CEME": ["CEME1P",
            "CEME2P",
            "CEME3P"],
   "PSPI": ["PSPI1P",
            "PSPI2P",
            "PSPI3P"],
   "LECO": ["LECO1P",
            "LECO2P",
            "LECO3P"],
   "MAVI": ["MAVI1P",
            "MAVI2P",
            "MAVI3P"],
   "MIOL": ["MIOL1P",
            "MIOL2P",
            "MIOL3P"],
   "CECO": ["CECO1P",
            "CECO2P",
            "CECO3P"],
   "XEAT": ["XEAT1P",
            "XEAT2P",
            "XEAT3P"]
}

SH_SAMPLES = {
   "CEME": ["CEME1S",
            "CEME2S",
            "CEME3S"],
   "PSPI": ["PSPI1S",
            "PSPI2S",
            "PSPI3S"],
   "LECO": ["LECO1S",
            "LECO2S",
            "LECO3S"],
   "MAVI": ["MAVI1S",
            "MAVI2S",
            "MAVI3S"],
   "MIOL": ["MIOL1S",
            "MIOL2S",
            "MIOL3S"],
   "CECO": ["CECO1S",
            "CECO2S",
            "CECO3S"],
   "XEAT": ["XEAT1S",
            "XEAT2S",
            "XEAT3S"]
}

COLORS = {
    'MIOL': '#aaaaaa',
    'XEAT': '#aaaaaa',
    'LECO': '#aaaaaa',
    'MAVI': '#ff9933',
    'PSPI': '#aaaaaa',
    'CEME': '#ff9933',
    'CECO': '#ff9933'
}

COLORMODELS = {
    "NONE": ['#666666'] * 7,
    "M6": ['#666666'] + ['#800080']*6,  
    "M5": ['#666666'] * 2 + ['#8787de'] * 5,
    "M4": ['#666666'] * 3 + ['#5599ff'] * 4,
    "R41": ['#666666'] * 3 + ['#008000', '#aaaaaa', '#008000', '#008000'],
    "MCC1": ['#666666'] * 3 + ['#ff7f2a', '#aaaaaa', '#ff7f2a', '#ff7f2a'],
    "MV": ['#666666'] * 3 + ['#ffdb4a'] + ['#666666']*3,
    "CE": ['#666666'] * 5 + ['#aa0000']*2,
}

SPECIESORDER = [
  'MIOL',
  'XEAT',
  'LECO',
  'MAVI',
  'PSPI',
  'CECO',
  'CEME',
]

COLORORDER = []
PC_FIELDORDER = []
SH_FIELDORDER = []
SPECIESCOLORORDER = []
for x in SPECIESORDER:
    SH_FIELDORDER.extend(SH_SAMPLES[x])
    PC_FIELDORDER.extend(PC_SAMPLES[x])
    COLORORDER.extend([COLORS[x]] * 3)
    SPECIESCOLORORDER.extend([COLORS[x]])

df = pd.read_csv(
    'Pease2022.PhyDGET_results.csv',
     delimiter=',', header=0, index_col=0, quotechar='"')

def gene_profilexgrid(outfile, genenames, rows=None):
    fig, ax = plt.subplots(6 if rows is None else rows, 5, 
        figsize=(12,16 if rows is None else 16/6*rows))
    j = 0
    k = 0
    for z, (genename, colormodel, genelabel) in enumerate(genenames):
        shdata = [2**df[x + ".nrm.SH"][genename] for x in SH_FIELDORDER]
        pcdata = [2**df[x + ".nrm.PC"][genename] for x in PC_FIELDORDER]
        shbf = str(round(df["deltaL.{}.SH".format(colormodel)][genename],2))
        pecbf = str(round(df["deltaL.{}.PC".format(colormodel)][genename],2))
        ymax = max(shdata + pcdata)
        ax[j,k].scatter(list(chain([(x, x, x) for x in range(7)])), (shdata),
            50, 
            marker='o', 
            color='none', 
            edgecolor='k',
            alpha=1,
            zorder=5
            )
        ax[j + 1,k].scatter(list(chain([(x, x, x) for x in range(7)])), (pcdata),
            50,
            marker='o', 
            color='none',
            edgecolor='k',
            zorder=5,
            alpha=1)
        shmeanvals = [np.mean([shdata[i], shdata[i+1], shdata[i+2]]) for i in range(0, len(shdata), 3)]
        shmax = max([np.max([shdata[i], shdata[i+1], shdata[i+2]]) for i in range(0, len(shdata), 3)])
        pcmeanvals = [np.mean([pcdata[i], pcdata[i+1], pcdata[i+2]]) for i in range(0, len(pcdata), 3)]
        pcmax = max([np.max([pcdata[i], pcdata[i+1], pcdata[i+2]]) for i in range(0, len(pcdata), 3)])
        shstderr = [np.std([shdata[i], shdata[i+1], shdata[i+2]])/np.sqrt(3) for i in range(0, len(shdata), 3)]
        pcstderr = [np.std([pcdata[i], pcdata[i+1], pcdata[i+2]])/np.sqrt(3) for i in range(0, len(pcdata), 3)]
        ax[j,k].scatter(range(7), list(shmeanvals),
                        150, 
                        color=COLORMODELS[colormodel], 
                        alpha = 1,
                        marker='_')
        ax[j + 1,k].scatter(range(7), 
                        list(pcmeanvals),
                        150, 
                        color=COLORMODELS[colormodel], 
                        alpha = 1,
                        marker='_')
        for i in range(7):
            ax[j,k].plot((i,i), (shmeanvals[i] - shstderr[i], shmeanvals[i] + shstderr[i]), 
                         color=COLORMODELS[colormodel][i],
                         linewidth=10,
                         alpha = 0.5
                        )
        for i in range(7):
            ax[j + 1,k].plot((i,i), (pcmeanvals[i-7] - pcstderr[i-7], pcmeanvals[i-7] + pcstderr[i-7]), 
                         color=COLORMODELS[colormodel][i],
                         linewidth=10,
                         alpha = 0.5
                        )
        specieslabels = [x[0] + x[2].lower() for x in SPECIESORDER]
        ax[j,k].margins(0.5,0.5)
        ax[j + 1,k].margins(0.5,0.5)
        ax[j,k].set_xticks(range(7))
        ax[j + 1,k].set_xticks(range(7))
        ax[j, k].set_xlim(-1,7.)
        ax[j + 1,k].set_xlim(-1,7)
        ax[j, k].set_ylim(-ymax*0.05, ymax*1.4)
        ax[j + 1,k].set_ylim(-ymax*0.05, ymax*1.4)
        ax[j,k].set_xticklabels(specieslabels)
        ax[j,k].tick_params(axis='x', rotation=-45)
        ax[j,k].tick_params(axis="both", labelsize=14)
        ax[j + 1,k].set_xticklabels(specieslabels)
        ax[j + 1,k].tick_params(axis="both", labelsize=14)
        ax[j + 1,k].tick_params(axis='x', rotation=-45)
        ax[j,k].tick_params(axis="both", labelsize=14)
        ax[j + 1,k].grid(axis='y')
        ax[j, k].grid(axis='y')
        ax[j, k].text(0.1, 0.78,
                      (genelabel if genelabel is not None
                      else genename) + "(S)\n{}".format(shbf), fontsize=14,
                      transform=ax[j, k].transAxes)   
        ax[j + 1, k].text(0.1 ,0.78,
              (genelabel if genelabel is not None
              else genename) + "(P)\n{}".format(pecbf), fontsize=14,
              transform=ax[j + 1, k].transAxes)
        ax[j + 1,0].set_ylabel("PEC cpm", size=14)
        ax[j, 0].set_ylabel("SH cpm", size=14)
        #plt.axvline(x = 6.5, color = 'grey')  
        k += 1
        if k == 5:
            j += 2
            k = 0
    
    plt.tight_layout()
    # plt.savefig(outfile, dpi=300)
    # plt.savefig(outfile.replace(".png", ".pdf"))
    plt.show()
    return ''

gene_profilexgrid("gene_supp_profiles1.png", [
    # ANC6 = 6
    ("CIAPIN1", "M6", None),
    ("PDK2", 'M6', None),
    ("PFKP", 'M6', None),
    ("YARS2", "M6", None),
    ("CIB2", "M6", None),
    ("LOC113993369", "M6", "KDM5C-L"),
    ("FOXF1", "M5", None),
    ("NAA35", "M5", None),
    ("SLC44A3", "M5", None),
    ("FOXO3", "M5", None),
    ("UBE3B", "M5", None),
    ("RETREG1", "M5", None),
    ("PPP1R3C", "M5", None),
    ("PPARGC1B", "M5", None),    
    ("CALM2", "M5", None),
])
 
gene_profilexgrid("gene_supp_profiles2.png", [   
    ("LOC113993297", "M5", "ERVFRD-1-L"),
    ("ADAMTS9", "M5", None),
    ("EAF2", "M5", None),
    ("RPAP2", "M4", None),
    ("FBXO4", "M4", None),
    ("PSMA7", "M4", None),
    ("PSMA2", "M4", None),
    ("DDRGK1", "M4", None),
    ("MLH1", "M4", None),
    ("ATP2A3", "M4", None),
    ("LOC114003417", "M4", "ATP2A1-L"),
    ("DPYSL5", "M4", None),
    ("STUM", "M4", None),
    ("KDM4B", "M4", None),
    ("LOC113999394", "R41", "TFCP2-L"),
])
    
gene_profilexgrid("gene_supp_profiles3.png", [
    ("CUL1", "R41", None),
    ("TTN", "R41", None),
    ("PSMC3", "R41", None),
    ("SPPL2A", "R41", None),
    ("TRDN", "R41", None),
    ("LOC113994824", "R41", "RYR1-L1"),
    ("LOC114001935", "R41", "RYR1-L2"),
    ("UBAC2", "R41", None),
    ("LOC113983589", "MCC1", "EIF4G3-L"),
    ("LOC113989613", "MCC1", "MYH3-L"),
    ("LOC114002148", "MCC1", "ROR1-L"),
    ("PSMC6", "MCC1", None),
    ("UFL1", "MCC1", None),
    ("BCO2", "MCC1", None),
    ("CCDC47", "MCC1", None),
])
 
gene_profilexgrid("gene_supp_profiles4.png", [   
    ("SRL", "MCC1", None),
    ("AR", "MCC1", None),
    ("ANK2", "MV", None),
    ("STAU2", "MV", None),
    ("MYBPH", "MV", None),
    ("TPRKB", "MV", None),
    ("UBXN1", "MV", None),
    ("ARFGAP3", "MV", None),
    ("HEMK1", "MV", None),
    ("PON2", "MV", None),
    ("CLRN1", "MV", None),
    ("HACD1", "MV", None),
])

 
gene_profilexgrid("gene_supp_profiles4b.png", [   
    ("NINJ2", "CE", None),
    ('STX2', "CE", None),
    ("LOC113990672", "CE", "PVALB-L1"),
    ("LOC113990673", "CE", "PVALB-L2"),
    ('HIPK3', "CE", None),
], rows=2)



In [ ]:
# import csv
from matplotlib import pyplot as plt
from matplotlib import cm
import matplotlib.colors as mcolors
import numpy as np
import pandas as pd
from IPython.display import display, Markdown, Latex
from matplotlib.markers import MarkerStyle

DATAORDER = ["deltaL.M6",
             "deltaL.M5",
             "deltaL.M4",
             "deltaL.MCC1",
             "deltaL.MCC2",
             "deltaL.R41",
             "deltaL.R42",
             "deltaL.R51",
             "deltaL.R52",
             "deltaL.XA",
             "deltaL.LC",
             "deltaL.MV",
             "deltaL.PP",
             "deltaL.CE"]

DATAORDER = [x + ".SH" for x in DATAORDER] + [x + ".PC" for x in DATAORDER]
MODELCOLOR = ['orange' if x.endswith('.SH') else 'blue' for x in DATAORDER]

m = MarkerStyle("d")
m._transform.rotate_deg(90)

PC_SAMPLES = {
   "CEME": ["CEME1P",
            "CEME2P",
            "CEME3P"],
   "PSPI": ["PSPI1P",
            "PSPI2P",
            "PSPI3P"],
   "LECO": ["LECO1P",
            "LECO2P",
            "LECO3P"],
   "MAVI": ["MAVI1P",
            "MAVI2P",
            "MAVI3P"],
   "MIOL": ["MIOL1P",
            "MIOL2P",
            "MIOL3P"],
   "CECO": ["CECO1P",
            "CECO2P",
            "CECO3P"],
   "XEAT": ["XEAT1P",
            "XEAT2P",
            "XEAT3P"]
}

SH_SAMPLES = {
   "CEME": ["CEME1S",
            "CEME2S",
            "CEME3S"],
   "PSPI": ["PSPI1S",
            "PSPI2S",
            "PSPI3S"],
   "LECO": ["LECO1S",
            "LECO2S",
            "LECO3S"],
   "MAVI": ["MAVI1S",
            "MAVI2S",
            "MAVI3S"],
   "MIOL": ["MIOL1S",
            "MIOL2S",
            "MIOL3S"],
   "CECO": ["CECO1S",
            "CECO2S",
            "CECO3S"],
   "XEAT": ["XEAT1S",
            "XEAT2S",
            "XEAT3S"]
}

COLORS = {
    'MIOL': '#6e750e',
    'XEAT': '#06c2ac',
    'LECO': '#0485d1',
    'MAVI': '#dbb40c',
    'PSPI': '#000000',
    'CEME': '#de87aa',
    'CECO': '#be0119'
}

COLORMODELS = {
    "NONE": ['#666666'] * 7,
    "M6": ['#666666'] + ['#800080']*6,  
    "M5": ['#666666'] * 2 + ['#8787de'] * 5,
    "M4": ['#666666'] * 3 + ['#5599ff'] * 4,
    "R41": ['#666666'] * 3 + ['#008000', '#aaaaaa', '#008000', '#008000'],
    "MCC1": ['#666666'] * 3 + ['#ff7f2a', '#aaaaaa', '#ff7f2a', '#ff7f2a'],
    "MV": ['#666666'] * 3 + ['#ffdb4a'] + ['#666666']*3,
    "CE": ['#666666'] * 5 + ['#aa0000']*2,
}

SPECIESORDER = [
  'MIOL',
  'XEAT',
  'LECO',
  'MAVI',
  'PSPI',
  'CECO',
  'CEME',
]

COLORORDER = []
PC_FIELDORDER = []
SH_FIELDORDER = []
SPECIESCOLORORDER = []
for x in SPECIESORDER:
    SH_FIELDORDER.extend(SH_SAMPLES[x])
    PC_FIELDORDER.extend(PC_SAMPLES[x])
    SPECIESCOLORORDER.extend([COLORS[x]])

    df = pd.read_csv(
    'Pease2022.PhyDGET_results.csv',
     delimiter=',', header=0, index_col=0, quotechar='"')

from itertools import chain
def gene_profilexgridnull(outfile, genenames):
    fig, ax = plt.subplots(6, 5, 
        figsize=(12,16))
    j = 0
    k = 0
    for z, (genename, colormodel, genelabel) in enumerate(genenames):
        shdata = [2**df[x + ".nrm.SH"][genename] for x in SH_FIELDORDER]
        pcdata = [2**df[x + ".nrm.PC"][genename] for x in PC_FIELDORDER]
        ymax = max(shdata + pcdata)
        ax[j,k].scatter(list(chain([(x, x, x) for x in range(7)])), (shdata),
            50, 
            marker='o', 
            color='none', 
            edgecolor='k',
            alpha=1,
            zorder=5
            )
        ax[j + 1,k].scatter(list(chain([(x, x, x) for x in range(7)])), (pcdata),
            50,
            marker='o', 
            color='none',
            edgecolor='k',
            zorder=5,
            alpha=1)
        shmeanvals = [np.mean([shdata[i], shdata[i+1], shdata[i+2]]) for i in range(0, len(shdata), 3)]
        shmax = max([np.max([shdata[i], shdata[i+1], shdata[i+2]]) for i in range(0, len(shdata), 3)])
        pcmeanvals = [np.mean([pcdata[i], pcdata[i+1], pcdata[i+2]]) for i in range(0, len(pcdata), 3)]
        pcmax = max([np.max([pcdata[i], pcdata[i+1], pcdata[i+2]]) for i in range(0, len(pcdata), 3)])
        shstderr = [np.std([shdata[i], shdata[i+1], shdata[i+2]])/np.sqrt(3) for i in range(0, len(shdata), 3)]
        pcstderr = [np.std([pcdata[i], pcdata[i+1], pcdata[i+2]])/np.sqrt(3) for i in range(0, len(pcdata), 3)]
        ax[j,k].scatter(range(7), list(shmeanvals),
                        150, 
                        color=SPECIESCOLORORDER,
                        alpha = 1,
                        marker='_')
        ax[j + 1,k].scatter(range(7), 
                        list(pcmeanvals),
                        150, 
                        color=SPECIESCOLORORDER,
                        alpha = 1,
                        marker='_')
        for i in range(7):
            ax[j,k].plot((i,i), (shmeanvals[i] - shstderr[i], shmeanvals[i] + shstderr[i]), 
                         color=SPECIESCOLORORDER[i],
                         linewidth=10,
                         alpha = 0.5
                        )
        for i in range(7):
            ax[j + 1,k].plot((i,i), (pcmeanvals[i-7] - pcstderr[i-7], pcmeanvals[i-7] + pcstderr[i-7]), 
                         color=SPECIESCOLORORDER[i],
                         linewidth=10,
                         alpha = 0.5
                        )
        specieslabels = [x[0] + x[2].lower() for x in SPECIESORDER]
        ax[j,k].margins(0.5,0.5)
        ax[j + 1,k].margins(0.5,0.5)
        ax[j,k].set_xticks(range(7))
        ax[j + 1,k].set_xticks(range(7))
        ax[j, k].set_xlim(-1,7.)
        ax[j + 1,k].set_xlim(-1,7)
        ax[j, k].set_ylim(-ymax*0.05, ymax*1.4)
        ax[j + 1,k].set_ylim(-ymax*0.05, ymax*1.4)
        ax[j,k].set_xticklabels(specieslabels)
        ax[j,k].tick_params(axis='x', rotation=-45)
        ax[j,k].tick_params(axis="both", labelsize=14)
        ax[j + 1,k].set_xticklabels(specieslabels)
        ax[j + 1,k].tick_params(axis="both", labelsize=14)
        ax[j + 1,k].tick_params(axis='x', rotation=-45)
        #ax[1,k].tick_params(axis='y', rotation=45)
        #ax[1,k].tick_params(axis='y', rotation=45)
        ax[j,k].tick_params(axis="both", labelsize=14)
        #ax[j,k].tick_params(bottom=False)
        ax[j + 1,k].grid(axis='y')
        ax[j, k].grid(axis='y')
        ax[j, k].text(0.1, 0.88,
                      (genelabel if genelabel is not None
                      else genename) + "(S)", fontsize=14,
                      transform=ax[j, k].transAxes)   
        ax[j + 1, k].text(0.1 ,0.88,
              (genelabel if genelabel is not None
              else genename) + "(P)", fontsize=14,
              transform=ax[j + 1, k].transAxes)
        ax[j + 1,0].set_ylabel("PEC cpm", size=14)
        ax[j, 0].set_ylabel("SH cpm", size=14)
        #plt.axvline(x = 6.5, color = 'grey')  
        k += 1
        if k == 5:
            j += 2
            k = 0
        

    
    plt.tight_layout()
    # plt.savefig(outfile, dpi=300)
    # plt.savefig(outfile.replace(".png", ".pdf"))
    plt.show()
    return ''

gene_profilexgridnull("gene_supp_profiles5.png", [   
    ("SVIL", "NONE", None),
    ("JPH2", "NONE", None),
    ("TNNC1", "NONE", None),
    ("TNNC2", "NONE", None),
    ("MYLK2", "NONE", None),
    ("MYBPC1", "NONE", None),
    ("TPM2", "NONE", None),
    ("TMOD1", "NONE", None),
    ("ACTA1", "NONE", None),
    ("LOC113984052", "NONE", "RYR1-L3"),
    ("LOC113984533", "NONE", "RYR1-L4"),
    ("LOC113985889", "NONE", "RYR1-L5"),
    ("LOC113999161", "NONE", "RYR1-L6"),
    ("RYR3", "NONE", None),
])
gene_profilexgridnull("gene_supp_profiles6.png", [   
    ("CAB39", "NONE", None),
    ("CACNA1S", "NONE", None),
    ("CACNA2D1", "NONE", None),
    ("CACNB1", "NONE", None),
    ("MTM1", "NONE", None),
    ("LOC114002581", "NONE", "MYO1B-L1"),
    ("LOC114002583", "NONE", "MYO1B-L2"),
    ("LOC114002585", "NONE", "MYH-L"),
    ("ACTC1", "NONE", None),
    ("TNNI2", "NONE", None),
    ("TNNT3", "NONE", None),
    ("ACTA1", "NONE", None),
    ("NEB", "NONE", None),
    ("OBSCN", "NONE", None)
    
])

gene_profilexgridnull("gene_supp_profiles7.png", [   
    ("ACAD11", "NONE", None),
    ("AFF1", "NONE", None),
    ("FOXRED1", "NONE", None),
    ("HOMER2", "NONE", None),
    ("PLCB1", "NONE", None),
    ("PPP1R3D", "NONE", None),
    ("PREPL", "NONE", None),
    ("SVIL", "NONE", None),
    ("CACNA1S", "NONE", None),
    ("CREBBP", "NONE", None),
    ("HSPA4L", "NONE", None),
    
])

In [ ]:
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
from sklearn.linear_model import LinearRegression

df_fs_sh = pd.read_csv('Pease2022.dge.grouped.snap.SH.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_anc4_sh = pd.read_csv('Pease2022.dge.grouped.M4.SH.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_anc5_sh = pd.read_csv('Pease2022.dge.grouped.M5.SH.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_anc6_sh = pd.read_csv('Pease2022.dge.grouped.M6.SH.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_mavi_sh = pd.read_csv('Pease2022.dge.grouped.MV.SH.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_cera_sh = pd.read_csv('Pease2022.dge.grouped.CE.SH.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_leco_sh = pd.read_csv('Pease2022.dge.grouped.LC.SH.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_xeat_sh = pd.read_csv('Pease2022.dge.grouped.XA.SH.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_fs_pc = pd.read_csv('Pease2022.dge.grouped.snap.PEC.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_anc4_pc = pd.read_csv('Pease2022.dge.grouped.M4.PEC.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_anc5_pc = pd.read_csv('Pease2022.dge.grouped.M5.PEC.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_anc6_pc = pd.read_csv('Pease2022.dge.grouped.M6.PEC.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_mavi_pc = pd.read_csv('Pease2022.dge.grouped.MV.PEC.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_cera_pc = pd.read_csv('Pease2022.dge.grouped.CE.PEC.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_leco_pc = pd.read_csv('Pease2022.dge.grouped.LC.PEC.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df_xeat_pc = pd.read_csv('Pease2022.dge.grouped.XA.PEC.limma.out', delimiter='\t', header=0, index_col=0, quotechar='"')
df = pd.read_csv('Pease2022.PhyDGET_results.csv', delimiter=',', header=0, index_col=0, quotechar='"')
df['pval_sh_fs'] = -1 * np.log10(df_fs_sh['adj.P.Val'])
df['pval_sh_anc4'] = -1 * np.log10(df_anc4_sh['adj.P.Val'])
df['pval_sh_anc5'] = -1 * np.log10(df_anc5_sh['adj.P.Val'])
df['pval_sh_anc6'] = -1 * np.log10(df_anc6_sh['adj.P.Val'])
df['pval_sh_mavi'] = -1 * np.log10(df_mavi_sh['adj.P.Val'])
df['pval_sh_cera'] = -1 * np.log10(df_cera_sh['adj.P.Val'])
df['pval_sh_mavi'] = -1 * np.log10(df_mavi_sh['adj.P.Val'])
df['pval_sh_leco'] = -1 * np.log10(df_leco_sh['adj.P.Val'])
df['pval_sh_xeat'] = -1 * np.log10(df_xeat_sh['adj.P.Val'])
df['pval_pc_fs'] = -1 * np.log10(df_fs_pc['adj.P.Val'])
df['pval_pc_anc4'] = -1 * np.log10(df_anc4_pc['adj.P.Val'])
df['pval_pc_anc5'] = -1 * np.log10(df_anc5_pc['adj.P.Val'])
df['pval_pc_anc6'] = -1 * np.log10(df_anc6_pc['adj.P.Val'])
df['pval_pc_mavi'] = -1 * np.log10(df_mavi_pc['adj.P.Val'])
df['pval_pc_cera'] = -1 * np.log10(df_cera_pc['adj.P.Val'])
df['pval_pc_mavi'] = -1 * np.log10(df_mavi_pc['adj.P.Val'])
df['pval_pc_leco'] = -1 * np.log10(df_leco_pc['adj.P.Val'])
df['pval_pc_xeat'] = -1 * np.log10(df_xeat_pc['adj.P.Val'])
xcritval = 1.5
ycritval = -1 * np.log10(1e-4)
LABELS = [
    'MC1\nSH',
    'R41\nSH',
    'M6\nSH',
    'M5\nSH',
    'MC1\nPEC',
    'R41\nPEC',
    'M6\nPEC',
    'M5\nPEC',
    'M4\nSH',
    'MV\nSH',
    'CE\nSH',
    'LC\nSH',
    'M4\nPEC',
    'MV\nPEC',
    'CE\nPEC',
    'LC\nPEC',
]
fig, ax = plt.subplots(4, 4, figsize=(12, 12))
for i, xfield, yfield, zlabel in zip(
        range(21),
        ('deltaL.MCC1.SH', 
         'deltaL.R41.SH', 
         'deltaL.M6.SH', 
         'deltaL.M5.SH', 
         'deltaL.MCC1.PC', 
         'deltaL.R41.PC', 
         'deltaL.M6.PC', 
         'deltaL.M5.PC', 
         'deltaL.M4.SH', 
         'deltaL.MV.SH',
         'deltaL.CE.PC',
         'deltaL.LC.SH',
         'deltaL.M4.PC', 
         'deltaL.MV.PC',
         'deltaL.CE.PC',
         'deltaL.LC.PC',
        ),
        ('pval_sh_fs', 
         'pval_sh_fs', 
         'pval_sh_anc6',
         'pval_sh_anc5',
         'pval_pc_fs', 
         'pval_pc_fs', 
         'pval_pc_anc6',
         'pval_pc_anc5', 
         'pval_sh_anc4', 
         'pval_sh_mavi',
         'pval_sh_cera',
         'pval_sh_leco',
         'pval_pc_anc4', 
         'pval_pc_mavi',
         'pval_pc_cera',
         'pval_pc_leco',
        ),
        LABELS
        ):
    j = i // 4
    i = i % 4
    dfx = df.filter((xfield, yfield, "bestmodel.SH")).dropna()
    xdata = np.array([dfx[xfield].values.tolist()]).reshape((-1, 1))
    ydata = np.array(dfx[yfield].values.tolist())
    regr = LinearRegression().fit(xdata, ydata)
    xfit = np.arange(-2, 5, 0.1).reshape((-1, 1))
    yfit = regr.predict(xfit)
    rsq = regr.score(xdata, ydata)
    dfsigb = dfx[(dfx[xfield] > xcritval) & (dfx[yfield] > ycritval)]
    dfsigx = dfx[(dfx[xfield] > xcritval) & (dfx[yfield] <= ycritval)]
    dfsigy = dfx[(dfx[xfield] <= xcritval) & (dfx[yfield] > ycritval)]
    dfsign = dfx[(dfx[xfield] <= xcritval) & (dfx[yfield] <= ycritval)]
    ax[j, i].scatter(dfsigx[xfield], dfsigx[yfield], c='#00d600', s=10, linewidth=0)
    ax[j, i].scatter(dfsigy[xfield], dfsigy[yfield], c='#0000cc', s=10, linewidth=0)
    ax[j, i].scatter(dfsigb[xfield], dfsigb[yfield], c='#ff00ff', s=10, linewidth=0)
    ax[j, i].scatter(dfsign[xfield], dfsign[yfield], c='none', s=10, alpha=0.5, edgecolor='grey')
    ax[j, i].text(0.1, 0.8, zlabel, transform=ax[j, i].transAxes, horizontalalignment='left',)
    ax[j, i].table(cellText=[['{}'.format(len(x)) for x in (dfsigy, dfsigb)],
                          ['{}'.format(len(x)) for x in (dfsign, dfsigx)],
                          ],
                          loc='top')
    if j == 3:
        ax[j, i].set_xlabel("Bayes Factor")
    if i == 0:
        ax[j, i].set_ylabel("$-$log$_{10}$($P$)")
plt.subplots_adjust(left=None, bottom=0.3, right=None, top=1, wspace=0.3, hspace=0.3)
plt.tight_layout()
#plt.savefig('limma_vs_regression.png', dpi=300)
plt.show()


In [ ]:
import csv
from itertools import combinations
from matplotlib import pyplot as plt
from matplotlib import cm
import matplotlib.colors as mcolors
from matplotlib.colors import LinearSegmentedColormap, ListedColormap
from mpl_toolkits.axes_grid1 import make_axes_locatable
import numpy as np
import pandas as pd

DATAORDER = ["deltaL.M6",
             "deltaL.M5",
             "deltaL.M4",
             "deltaL.MCC1",
             "deltaL.MCC2",
             "deltaL.R41",
             "deltaL.R42",
             "deltaL.R51",
             "deltaL.R52",
             "deltaL.XA",
             "deltaL.LC",
             "deltaL.MV",
             "deltaL.PP",
             "deltaL.CE"]

SPECIES = {"CEME": ["CEME1",
                    "CEME2",
                    "CEME3"],
           "PSPI": ["PSPI1",
                    "PSPI2",
                    "PSPI3"],
           "LECO": ["LECO1",
                    "LECO2",
                    "LECO3"],
           "MAVI": ["MAVI1",
                    "MAVI2",
                    "MAVI3"],
           "MIOL": ["MIOL1",
                    "MIOL2",
                    "MIOL3"],
           "CECO": ["CECO1",
                    "CECO2",
                    "CECO3"],
           "XEAT": ["XEAT1",
                    "XEAT2",
                    "XEAT3"]}

COLORS = {'MIOL': '#6e750e',
          'XEAT': '#000000',
          'LECO': '#0485d1',
          'MAVI': '#dbb40c',
          'PSPI': '#95a3a6',
          'CEME': '#ff796c',
          'CECO': '#be0119'
          }

BOTHDATAORDER = [x + ".SH" for x in DATAORDER] + [x + ".PC" for x in DATAORDER]

SPECIESORDER = ['MIOL', 'XEAT', 'LECO', 'MAVI', 'PSPI', 'CEME', 'CECO']
COLORORDER = []
FIELDORDER = []
for x in SPECIESORDER:
    FIELDORDER.extend(SPECIES[x])
    COLORORDER.extend([COLORS[x]] * 3)
df = pd.read_csv('Pease2022.PhyDGET_results.csv', delimiter=',', header=0, index_col=0, quotechar='"')

MODELS = ['M6', 'M5', 'M4', 'R41', 'MCC1', 'MCC2', 'MV', 'PP', 'CE']

fig, ax = plt.subplots(8, 8, sharex='col', sharey='row', figsize=(16,16))
for (i, j) in combinations(range(len(MODELS)), 2):
    model0 = "deltaL." + MODELS[i] + ".SH"
    model1 = "deltaL." + MODELS[j] + ".SH"
    psig = (df[model1] >= 1.5).values.tolist()
    ssig = (df[model0] >= 1.5).values.tolist()
    intersect = [psig[x] is True and sval is True for x, sval in enumerate(ssig)]
    ponly = [psig[x] is True and sval is False for x, sval in enumerate(ssig)]
    sonly = [psig[x] is False and sval is True for x, sval in enumerate(ssig)]
    neither = [psig[x] is False and sval is False for x, sval in enumerate(ssig)]
    ax[i,j-1].scatter(df[model1][intersect], df[model0][intersect], c='magenta', s=10)
    ax[i,j-1].scatter(df[model1][ponly], df[model0][ponly], c='#00d600', s=10)
    ax[i,j-1].scatter(df[model1][sonly], df[model0][sonly], c='#0000cc', s=10)
    ax[i,j-1].scatter(df[model1][neither], df[model0][neither], c='gray', s=10)        
    maxval = max(max(df[model1]), max(df[model0])) * 1.1
    minval = min(min(df[model1]), min(df[model0])) * 1.1
    ax[i,j-1].plot((minval, maxval),(minval, maxval), 'k--')
    ax[i,j-1].set_xlim(minval, maxval)
    ax[i,j-1].set_ylim(minval, maxval)
    label0 = model0.replace("deltaL.", "").replace("REV","R").replace("MCC",'MC').replace("MAVI", "MV").replace("PSPI","PP").replace("CERA", "CE").replace("ANC", "M").replace(".SH","")
    label1 = model1.replace("deltaL.", "").replace("REV","R").replace("MCC",'MC').replace("MAVI", "MV").replace("PSPI","PP").replace("CERA", "CE").replace("ANC", "M").replace(".SH","")
    ax[i,j-1].text(0.1, 0.8, "y:{}\nx:{}".format(label0, label1), transform=ax[i, j-1].transAxes)
    if i == j-1:
        ax[i,j-1].set_xlabel(model1.replace("deltaL.", "BF.").replace("REV","R").replace("MCC",'MC').replace("MAVI", "MV").replace("PSPI","PP").replace("CERA", "CE").replace("ANC", "M").replace(".SH",""))
        ax[i,j-1].set_ylabel(model0.replace("deltaL.", "BF.").replace("REV","R").replace("MCC",'MC').replace("MAVI", "MV").replace("PSPI","PP").replace("CERA", "CE").replace("ANC", "M").replace(".SH",""))
plt.tight_layout()
#plt.savefig("phydgetcor.png")
plt.show()